<a href="https://colab.research.google.com/github/Adosha/DAT7/blob/master/Copy_of_mlcourse_ai_a2_catboost_starter_edited.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<center>
<img src="https://habrastorage.org/files/fd4/502/43d/fd450243dd604b81b9713213a247aa20.jpg" />
</center> 
     
## <center>  [mlcourse.ai](https://mlcourse.ai) – Open Machine Learning Course 

#### <center> Author: [Yury Kashnitsky](https://yorko.github.io) (@yorko) 

# <center>Assignment #2. Fall 2019
## <center> Part 2. Gradient boosting

**In this assignment, you're asked to beat a baseline in the ["Flight delays" competition](https://www.kaggle.com/c/flight-delays-fall-2018).**

This time we decided to share a pretty decent CatBoost baseline, you'll have to improve the provided solution.

Prior to working on the assignment, you'd better check out the corresponding course material:
 1. [Classification, Decision Trees and k Nearest Neighbors](https://nbviewer.jupyter.org/github/Yorko/mlcourse_open/blob/master/jupyter_english/topic03_decision_trees_kNN/topic3_decision_trees_kNN.ipynb?flush_cache=true), the same as an interactive web-based [Kaggle Kernel](https://www.kaggle.com/kashnitsky/topic-3-decision-trees-and-knn) 
 2. Ensembles:
  - [Bagging](https://nbviewer.jupyter.org/github/Yorko/mlcourse_open/blob/master/jupyter_english/topic05_ensembles_random_forests/topic5_part1_bagging.ipynb?flush_cache=true), the same as a [Kaggle Kernel](https://www.kaggle.com/kashnitsky/topic-5-ensembles-part-1-bagging)
  - [Random Forest](https://nbviewer.jupyter.org/github/Yorko/mlcourse_open/blob/master/jupyter_english/topic05_ensembles_random_forests/topic5_part2_random_forest.ipynb?flush_cache=true), the same as a [Kaggle Kernel](https://www.kaggle.com/kashnitsky/topic-5-ensembles-part-2-random-forest)
  - [Feature Importance](https://nbviewer.jupyter.org/github/Yorko/mlcourse_open/blob/master/jupyter_english/topic05_ensembles_random_forests/topic5_part3_feature_importance.ipynb?flush_cache=true), the same as a [Kaggle Kernel](https://www.kaggle.com/kashnitsky/topic-5-ensembles-part-3-feature-importance)
 3. - [Gradient boosting](https://nbviewer.jupyter.org/github/Yorko/mlcourse_open/blob/master/jupyter_english/topic10_boosting/topic10_gradient_boosting.ipynb?flush_cache=true), the same as a [Kaggle Kernel](https://www.kaggle.com/kashnitsky/topic-10-gradient-boosting) 
   - Logistic regression, Random Forest, and LightGBM in the "Kaggle Forest Cover Type Prediction" competition: [Kernel](https://www.kaggle.com/kashnitsky/topic-10-practice-with-logit-rf-and-lightgbm) 
 4. You can also practice with demo assignments, which are simpler and already shared with solutions:
  - "Decision trees with a toy task and the UCI Adult dataset": [assignment](https://www.kaggle.com/kashnitsky/a3-demo-decision-trees) + [solution](https://www.kaggle.com/kashnitsky/a3-demo-decision-trees-solution)
  - "Logistic Regression and Random Forest in the credit scoring problem": [assignment](https://www.kaggle.com/kashnitsky/assignment-5-logit-and-rf-for-credit-scoring) + [solution](https://www.kaggle.com/kashnitsky/a5-demo-logit-and-rf-for-credit-scoring-sol)
 5. There are also 7 video lectures on trees, forests, boosting and their applications: [mlcourse.ai/video](https://mlcourse.ai/video) 
 6. mlcourse.ai tutorials on [categorical feature encoding](https://www.kaggle.com/waydeherman/tutorial-categorical-encoding) (by Wayde Herman) and [CatBoost](https://www.kaggle.com/mitribunskiy/tutorial-catboost-overview) (by Mikhail Tribunskiy)
 7. Last but not the least: [Public Kernels](https://www.kaggle.com/c/flight-delays-fall-2018/notebooks) in this competition

### Your task is to:
 1. beat **"A2 baseline (10 credits)"** on Public LB (**0.75914** LB score)
 2. rename your [team](https://www.kaggle.com/c/flight-delays-fall-2018/team) in full accordance with A1 and the [course rating](https://docs.google.com/spreadsheets/d/15e1K0tg5ponA5R6YQkZfihrShTDLAKf5qeKaoVCiuhQ/) (to appear on 16.09.2019)
 
This task is intended to be relatively easy. Here you are not required to upload your reproducible solution.
 
### <center> Deadline for A2: 2019 October 6, 20:59 CET (London time)

In [0]:
!pip install catboost

     |████████████████████████████████| 62.6MB 38.7MB/s 


In [0]:
import warnings
import numpy as np
import pandas as pd
from pathlib import Path
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score
from catboost import CatBoostClassifier

In [0]:


#train_df.tail()

## **Create only one feature - “flight” (this you need to improve - add more features)**

In [136]:
PATH_TO_DATA = Path('')
train_df = pd.read_csv(PATH_TO_DATA / 'flight_delays_train.csv')
test_df = pd.read_csv(PATH_TO_DATA / 'flight_delays_test.csv')

train_df['flight'] = train_df['Origin'] + '-->' + train_df['Dest']
test_df['flight'] = test_df['Origin'] + '-->' + test_df['Dest']

train_df['Origin_Carrier'] = train_df['Origin'] + '_' + train_df['UniqueCarrier'].astype('str')
test_df['Origin_Carrier'] = test_df['Origin'] + '_' + test_df['UniqueCarrier'].astype('str')

train_df['Dep_hour'] =  train_df['DepTime']//100
train_df['Dep_hour'].replace(to_replace=[24,25], value=0, inplace=True)
test_df['Dep_hour'] =  test_df['DepTime']//100
test_df['Dep_hour'].replace(to_replace=[24,25], value=0, inplace=True)

train_df['Dep_hour'] = train_df['Dep_hour'].astype('str')
test_df['Dep_hour'] = test_df['Dep_hour'].astype('str')

train_df['Dep_minute'] =  train_df['DepTime']%100
train_df['Dep_minute'] =  train_df['Dep_minute']//10
test_df['Dep_minute'] =  test_df['DepTime']%100
test_df['Dep_minute'] =  test_df['Dep_minute']//10

train_df['Origin_10min'] = train_df['Origin'] + '_' + train_df['Dep_minute'].astype('str')
test_df['Origin_10min'] = test_df['Origin'] + '_' + test_df['Dep_minute'].astype('str')

train_df['Destination_10min'] = train_df['Dest'] + '_' + train_df['Dep_minute'].astype('str')
test_df['Destination_10min'] = test_df['Dest'] + '_' + test_df['Dep_minute'].astype('str')

train_df['Carrier_10min'] = train_df['UniqueCarrier'] + '_' + train_df['Dep_minute'].astype('str')
test_df['Carrier_10min'] = test_df['UniqueCarrier'] + '_' + test_df['Dep_minute'].astype('str')



train_df['Dep_hour_10min'] =  train_df['Dep_hour'] + '_' + train_df['Dep_minute'].astype('str')
test_df['Dep_hour_10min'] =  test_df['Dep_hour'] + '_' + test_df['Dep_minute'].astype('str')

train_df['Month_n'] = train_df['Month'].str[2:].astype('int')
train_df['DayofMonth_n'] = train_df['DayofMonth'].str[2:].astype('int')
train_df['DayOfWeek_n'] = train_df['DayOfWeek'].str[2:].astype('int')
test_df['Month_n'] = test_df['Month'].str[2:].astype('int')
test_df['DayofMonth_n'] = test_df['DayofMonth'].str[2:].astype('int')
test_df['DayOfWeek_n'] = test_df['DayOfWeek'].str[2:].astype('int')

train_df['Month_DayofMonth'] = train_df['Month_n'].astype('str')  + '_' + train_df['DayofMonth_n'].astype('str')
test_df['Month_DayofMonth'] = test_df['Month_n'].astype('str')  + '_' + test_df['DayofMonth_n'].astype('str')

train_df['Month_DayofMonth_dephour'] = train_df['Month_DayofMonth'] + '_' + train_df['Dep_hour'].astype('str')
test_df['Month_DayofMonth_dephour'] = test_df['Month_DayofMonth'] + '_' + test_df['Dep_hour'].astype('str')

train_df['Origin_hour10min'] = train_df['Origin'] + '_' + train_df['Dep_hour_10min'].astype('str')
test_df['Origin_hour10min'] = test_df['Origin'] + '_' + test_df['Dep_hour_10min'].astype('str')

train_df['Origin_dephour'] = train_df['Origin'] + '_' + train_df['Dep_hour_10min'].astype('str')
test_df['Origin_dephour'] = test_df['Origin'] + '_' + test_df['Dep_hour_10min'].astype('str')

train_df['Destination_dephour'] = train_df['Dest'] + '_' + train_df['Dep_hour_10min'].astype('str')
test_df['Destination_dephour'] = test_df['Dest'] + '_' + test_df['Dep_hour_10min'].astype('str')


#timeOfday={'0':'Night', '1':'Night', '2':'Night', '3':'Night', '4':'Night', '5':'Night', '6':'Morning','7':'Morning', '8':'Morning', '9':'Morning', '10':'Morning', '11':'Morning', '12':'Midtime', '13':'Midtime', '14':'Midtime', '15':'Midtime', '16':'Midtime', '17':'Midtime', '18':'Evening', '19':'Evening', '20':'Evening', '21':'Evening', '22':'Evening', '23':'Evening'}
timeOfday={'0':'nodelay', '1':'nodelay', '2':'nodelay', '3':'nodelay', '4':'nodelay', '5':'nodelay', '6':'delay','7':'delay', '8':'delay', '9':'delay', '10':'delay', '11':'delay', '12':'delay', '13':'delay', '14':'delay', '15':'delay', '16':'delay', '17':'delay', '18':'delay', '19':'delay', '20':'delay', '21':'delay', '22':'delay', '23':'nodelay'}
train_df['timeOfday'] = train_df['Dep_hour'].map(timeOfday)
test_df['timeOfday'] = test_df['Dep_hour'].map(timeOfday)

train_df['DayofMonth_timeOfday'] = train_df['DayofMonth_n'].astype('str') + '_' + train_df['timeOfday'].astype('str')
test_df['DayofMonth_timeOfday'] = test_df['DayofMonth_n'].astype('str') + '_' + test_df['timeOfday'].astype('str')

train_df['Origin_timeOfday'] = train_df['Origin'] + '_' + train_df['timeOfday'].astype('str')
test_df['Origin_timeOfday'] = test_df['Origin'] + '_' + test_df['timeOfday'].astype('str')

train_df['Destination_timeOfday'] = train_df['Dest'] + '_' + train_df['timeOfday'].astype('str')
test_df['Destination_timeOfday'] = test_df['Dest'] + '_' + test_df['timeOfday'].astype('str')

train_df['Carrier_timeOfday'] = train_df['UniqueCarrier'] + '_' + train_df['timeOfday'].astype('str')
test_df['Carrier_timeOfday'] = test_df['UniqueCarrier'] + '_' + test_df['timeOfday'].astype('str')



train_df['Carrier_DayofMonth_time'] = train_df['UniqueCarrier'] + '_' + train_df['DayofMonth_n'].astype('str')
test_df['Carrier_DayofMonth_time'] = test_df['UniqueCarrier'] + '_' + test_df['DayofMonth_n'].astype('str')

######### 0.778

train_df['UniqueCarrier_Origin_Distance'] = train_df['UniqueCarrier']  + '-->' + train_df['Origin']  + '-->' + train_df['Distance'].astype('str')
test_df['UniqueCarrier_Origin_Distance'] = test_df['UniqueCarrier'] + '-->' + test_df['Origin']  + '-->' + test_df['Distance'].astype('str')

train_df['UniqueCarrier_Origin'] = train_df['UniqueCarrier']  + '-->' + train_df['Origin'] 
test_df['UniqueCarrier_Origin'] = test_df['UniqueCarrier'] + '-->' + test_df['Origin']


train_df['UniqueCarrier_Destination'] = train_df['UniqueCarrier']  + '-->' + train_df['Dest'] 
test_df['UniqueCarrier_Destination'] = test_df['UniqueCarrier'] + '-->' + test_df['Dest']

train_df['DayOfWeek_hour10min'] = train_df['DayOfWeek'] + '_' + train_df['Dep_hour_10min'].astype('str')
test_df['DayOfWeek_hour10min'] = test_df['DayOfWeek'] + '_' + test_df['Dep_hour_10min'].astype('str')


#train_df['Destination_DayofMonth'] = train_df['Dest'] + '_' + train_df['DayofMonth_n'].astype('str')
#test_df['Destination_DayofMonth'] = test_df['Dest'] + '_' + test_df['DayofMonth_n'].astype('str')

#train_df['Origin_DayofMonth'] = train_df['Origin'] + '_' + train_df['DayofMonth_n'].astype('str')
#test_df['Origin_DayofMonth'] = test_df['Origin'] + '_' + test_df['DayofMonth_n'].astype('str')

train_df['UniqueCarrier_DayofMonth'] = train_df['UniqueCarrier'] + '_' + train_df['DayofMonth_n'].astype('str')
test_df['UniqueCarrier_DayofMonth'] = test_df['UniqueCarrier'] + '_' + test_df['DayofMonth_n'].astype('str')

train_df['Carrier_dephour'] = train_df['UniqueCarrier'] + '_' + train_df['Dep_hour'].astype('str')
test_df['Carrier_dephour'] = test_df['UniqueCarrier'] + '_' + test_df['Dep_hour'].astype('str')

train_df['UniqueCarrier_Distance'] = train_df['UniqueCarrier']  + '_' + train_df['Distance'].astype('str')
test_df['UniqueCarrier_Distance'] = test_df['UniqueCarrier'] + '_' + test_df['Distance'].astype('str')

train_df['Dep_hour'] = train_df['Dep_hour'].astype('int')
test_df['Dep_hour'] = test_df['Dep_hour'].astype('int')







#train_df = train_df.drop('Dep_hour', axis=1)
#test_df = test_df.drop('Dep_hour', axis=1)
train_df = train_df.drop('Month_n', axis=1)
test_df = test_df.drop('Month_n', axis=1)
train_df = train_df.drop('DayofMonth_n', axis=1)
test_df = test_df.drop('DayofMonth_n', axis=1)
train_df = train_df.drop('DayOfWeek_n', axis=1)
test_df = test_df.drop('DayOfWeek_n', axis=1)

train_df = train_df.drop('Dep_minute', axis=1)
test_df = test_df.drop('Dep_minute', axis=1)
#train_df = train_df.drop('DepTime', axis=1)
#test_df = test_df.drop('DepTime', axis=1)

X_train = train_df.drop('dep_delayed_15min', axis=1)
y_train = train_df['dep_delayed_15min'].map({'Y': 1, 'N': 0})
X_test = test_df

columns = list(X_train)
i=0
for column in columns:    
    column_new = str(i) + '_' + column
    i += 1
    X_train.rename(columns={column:column_new}, inplace=True)
    X_test.rename(columns={column:column_new}, inplace=True)

X_train.tail()


0_Month 1_DayofMonth  ... 31_Carrier_dephour  32_UniqueCarrier_Distance
99995     c-5          c-4  ...              OO_16                     OO_199
99996     c-1         c-18  ...               CO_8                     CO_884
99997     c-1         c-24  ...              NW_19                    NW_1076
99998     c-4         c-27  ...              MQ_15                     MQ_140
99999    c-11         c-17  ...              WN_18                     WN_605

[5 rows x 33 columns]

In [0]:
categ_feat_idx = np.where(train_df.drop('dep_delayed_15min', axis=1).dtypes == 'object')[0]
#categ_feat_idx.tolist()
X_train_part, X_valid, y_train_part, y_valid = train_test_split(X_train, y_train, 
                                                                test_size=0.3, 
                                                                random_state=17)

SEED = 17
ignored_features = [20]
#ignored_features = [0,1,24,3,15,17,25,14,19,4,7,19,27,18,23]
params = {#'loss_function':'Logloss',
          #'eval_metric':'AUC',
          'n_estimators':10000,
          'learning_rate': 0.015,
          #'depth' : 8,
          #'grow_policy': 'Lossguide', 
          #'l2_leaf_reg' : 2.9,
          'cat_features': categ_feat_idx,
          'ignored_features': ignored_features,
          'task_type': 'GPU',
          #'border_count': 32,
          #'verbose': 200,
          'early_stopping_rounds': 500,
          'silent' : True,
          'random_seed': SEED
         }

ctb = CatBoostClassifier(**params)
                         


In [0]:
%%time

from catboost import Pool

train_data = Pool(data=X_train_part,
                  label=y_train_part,
                  cat_features=categ_feat_idx
                 )

valid_data = Pool(data=X_valid,
                  label=y_valid,
                  cat_features=categ_feat_idx
                 )


ctb.fit(train_data,
        #cat_features=categ_feat_idx,
          eval_set=valid_data,
          use_best_model=True,
          plot=True
         );

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [0]:
ctb_valid_pred = ctb.predict_proba(X_valid)[:, 1]

In [0]:
roc_auc_score(y_valid, ctb_valid_pred)

In [0]:
ctb.get_feature_importance(prettified=True)



**Train on the whole train set, make prediction on the test set. We got ~0.734 in the competition - "Catboost starter" baseline**

In [0]:
%%time
ctb.fit(X_train, y_train,
        cat_features=categ_feat_idx);

In [0]:
ctb_test_pred = ctb.predict_proba(X_test)[:, 1]

In [0]:
with warnings.catch_warnings():
    warnings.simplefilter("ignore")
    
    sample_sub = pd.read_csv(PATH_TO_DATA / 'sample_submission.csv', 
                             index_col='id')
    sample_sub['dep_delayed_15min'] = ctb_test_pred
    sample_sub.to_csv('ctb_pred03_6.csv')
    
from IPython.display import FileLink
FileLink('ctb_pred03_6.csv')

/content/ctb_pred03_5.csv

In [0]:
!head ctb_pred03_6.csv

id,dep_delayed_15min
0,0.009827136669164379
1,0.11545799538136498
2,0.0463712071002693
3,0.3702820811002685
4,0.2069329929925136
5,0.022263141595041006
6,0.14040069247067566
7,0.48791241024621884
8,0.3086570920849654


Now's your turn! Go and improve the model to beat **"A2 baseline (10 credits)"** - **0.75914** LB score. It's crucial to come up with some good features. 

For discussions, stick to the **#a2_kaggle_fall2019** thread in the **mlcourse_ai_news** [ODS Slack](http://opendatascience.slack.com) channel. Serhii Romanenko (@serhii_romanenko) will be there to help. 

Welcome to Kaggle!

<img src='https://habrastorage.org/webt/fs/42/ms/fs42ms0r7qsoj-da4x7yfntwrbq.jpeg' width=50%>
*from the ["Nerd Laughing Loud"](https://www.kaggle.com/general/76963) thread.*